<style>
H3{
    color:black;
}
</style>

<center><H1 style="color:black";style="text-align: center;">Syarah Scraping</H1>

<H2 style="color:black;">(Saudi Cars Marketplace)</H2></center>

<H3 style="color:black;">The Website</H3>

[Syarah - Used Cars](https://syarah.com/%D8%B3%D9%8A%D8%A7%D8%B1%D8%A7%D8%AA-%D9%85%D8%B3%D8%AA%D8%B9%D9%85%D9%84%D8%A9)

### Importing libraries

In [374]:
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
import time
import os
import requests
import pandas as pd

### Scraping the link pages for used cars from the main page

In [7]:
driver = webdriver.Chrome(r'chromedriver')

driver.get('https://syarah.com/%D8%B3%D9%8A%D8%A7%D8%B1%D8%A7%D8%AA-%D9%85%D8%B3%D8%AA%D8%B9%D9%85%D9%84%D8%A9')

while True:
    # Scroll down to bottom
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")

    # Wait to load page
    time.sleep(5)
        
    # Calculate new scroll height and compare with last scroll height
    new_height = driver.execute_script("return document.body.scrollHeight")
    if new_height == last_height:
        break
    last_height = new_height

# Create list to save links
list_of_hrefs = []

# Get all components inside the tag that has a class name "allCarsResult"
content_blocks = driver.find_elements_by_class_name("allCarsResult")

for block in content_blocks:
    links = block.find_elements_by_tag_name('a') # Get all a tags
    for l in links:
        list_of_hrefs.append(l.get_attribute('href')) # Get the link from href attribute and add it to the list

print(list_of_hrefs)

time.sleep(3)

driver.quit()

['https://syarah.com/%D9%83%D8%B1%D8%A7%D9%8A%D8%B3%D9%84%D8%B1_C300_%D8%B3%D8%B9%D9%88%D8%AF%D9%8A_2018_%D9%81%D9%84/car-10447460', 'https://syarah.com/%D9%86%D9%8A%D8%B3%D8%A7%D9%86_%D8%A8%D8%A7%D8%AA%D8%B1%D9%88%D9%84_%D8%B1%D8%A8%D8%B9_2016_%D8%B3%D8%B9%D9%88%D8%AF%D9%8A_%D9%81%D9%84/car-10447492', 'https://syarah.com/online/%D9%86%D9%8A%D8%B3%D8%A7%D9%86_%D8%B5%D9%86%D9%8A_SV_2019_%D8%B3%D8%AA%D8%A7%D9%86%D8%AF%D8%B1/car-73516', 'https://syarah.com/online/%D9%87%D9%88%D9%86%D8%AF%D8%A7%D9%8A_%D8%A7%D9%84%D9%86%D8%AA%D8%B1%D8%A7_GL_2019_%D8%B3%D8%AA%D8%A7%D9%86%D8%AF%D8%B1/car-73118', 'https://syarah.com/online/%D9%87%D9%88%D9%86%D8%AF%D8%A7%D9%8A_%D8%A7%D9%84%D9%86%D8%AA%D8%B1%D8%A7_GL_2019_%D9%86%D8%B5_%D9%81%D9%84/car-73130', 'https://syarah.com/online/%D9%83%D9%8A%D8%A7_%D8%B1%D9%8A%D9%88_LX_2017_%D8%B3%D8%AA%D8%A7%D9%86%D8%AF%D8%B1/car-50669', 'https://syarah.com/%D9%87%D9%88%D9%86%D8%AF%D8%A7_%D8%A7%D9%83%D9%88%D8%B1%D8%AF_2018_%D8%B3%D8%B9%D9%88%D8%AF%D9%8A_%D9%81%D9%84/car-

In [253]:
len(list_of_hrefs) # Size of list

9015

### Create an empty dataframe with specific columns

In [309]:
df = pd.DataFrame([], columns = ['Link', 'Make', 'Type', 'Year', 'Origin', 'Color', 'Options', 'Engine_Size', 'Fuel_Type', 'Gear_Type', 'Condition', 'Mileage', 'Region', 'Price'])

### Create an empty dictionary to save details of the car

In [311]:
data_dict = {"Link":[],"Make":[],"Type":[],"Year":[],"Origin":[],"Color":[],"Options":[],"Engine_Size":[],"Fuel_Type":[],"Gear_Type":[],"Condition":[],"Mileage":[],"Region":[],"Price":[]}

### Function for checking if xPath available in the HTML code or not

In [312]:
from selenium.common.exceptions import NoSuchElementException        
def check_exists_by_xpath(xpath):
    try:
        driver.find_element_by_xpath(xpath)
    except NoSuchElementException:
        return False
    return True

### Scraping the details of used cars from each link

In [370]:
for i, link in enumerate(list_of_hrefs[5000:9015]):
    
    print(i," ", link)
    driver.get(link)
    
    CheckPage = check_exists_by_xpath('//section[@class="carInfoCC"]') # Check if "carInfoCC" element in the page
    if CheckPage: # True
        data_dict["Link"].append(link)
        
        # Get all div elements inside "carDetailesCC"
        maindeatils = driver.find_element_by_class_name('carDetailesCC')
        divdeatils = maindeatils.find_elements_by_tag_name('div')
        
        # Pass all div elements
        for l in divdeatils:
            lables = l.find_elements_by_tag_name('label') # Get the label
            for lable in lables:
                # Cleaning the label
                CleanLable = lable.text
                CleanLable=CleanLable.replace(':', '') # Remove :
                CleanLable=CleanLable.strip() # Remove all spaces
                print(CleanLable)
            values = l.find_elements_by_tag_name('strong') # Get the value
            for value in values:
                print(value.text)
                
                # Check from the label name. Then, insert the value into the dictionary
                if  (CleanLable == 'Make')  | (CleanLable == 'الماركة'):
                    data_dict["Make"].append(value.text)
                elif (CleanLable == 'Type') | (CleanLable == 'النوع'):
                    data_dict["Type"].append(value.text)
                elif (CleanLable == 'Year') | (CleanLable == 'الموديل') | (CleanLable == 'سنة الصنع'):
                    data_dict["Year"].append(value.text)
                elif (CleanLable == 'Origin') | (CleanLable == 'الوارد'):
                    data_dict["Origin"].append(value.text)
                elif (CleanLable == 'Color') | (CleanLable == 'اللون'):
                    data_dict["Color"].append(value.text)
                elif (CleanLable == 'Options') | (CleanLable == 'المواصفات'):
                    data_dict["Options"].append(value.text)
                elif (CleanLable == 'Engine Size') | (CleanLable == 'حجم المحرك') | (CleanLable == 'سعة المحرك'):
                    data_dict["Engine_Size"].append(value.text)
                elif (CleanLable == 'Fuel Type') | (CleanLable == 'نوع الوقود'):
                    data_dict["Fuel_Type"].append(value.text)
                elif (CleanLable == 'Gear Type') | (CleanLable == 'نوع القير'):
                    data_dict["Gear_Type"].append(value.text)
                elif (CleanLable == 'Condition') | (CleanLable == 'الحالة'):
                    data_dict["Condition"].append(value.text)
                elif (CleanLable == 'Mileage') | (CleanLable== 'الممشى'):
                    CleanValue = value.text
                    # Cleaning the value
                    CleanValue=CleanValue.replace('كم', '') # Remove كم
                    CleanValue=CleanValue.replace('KM', '') # Remove Km
                    CleanValue=CleanValue.replace('ميل', '') # Remove ميل
                    CleanValue=CleanValue.replace(',', '') # Remove ,
                    CleanValue=CleanValue.strip() # Remove all spaces
                    data_dict["Mileage"].append(CleanValue)
                elif (CleanLable == 'Region') | (CleanLable == 'المنطقة'):
                    data_dict["Region"].append(value.text)
        
        # We have two elements to get the price. So, first, we will check the xPath
        CheckPath = check_exists_by_xpath('//div[@class="SOLacPrice"]/strong')
        if CheckPath: # True
            price = driver.find_elements_by_xpath('//div[@class="SOLacPrice"]/strong') # If there is discount
            print(price[1].text)
            CleanValue = price[1].text
        else: # False (No discount)
            price = driver.find_element_by_css_selector('strong.priceBeforeTax ')
            print(price.text)
            CleanValue = price.text
            
        # Cleaning the value
        CleanValue=CleanValue.replace('ريال', '') # Remove ريال
        CleanValue=CleanValue.replace('SAR', '') # Remove SAR
        CleanValue=CleanValue.replace(',', '') # Remove ,
        CleanValue=CleanValue.strip() # Remove all spaces
        data_dict["Price"].append(CleanValue)

        print('=====================================================================================')
        time.sleep(5)
        
    else: # False ("carInfoCC" element not available in the page)
        continue

driver.quit()

0   https://syarah.com/%D9%83%D9%8A%D8%A7_%D8%B3%D8%A8%D9%88%D8%B1%D8%AA%D8%A7%D8%AC_2015/car-10448956
الماركة
كيا
النوع
سبورتاج
الموديل
2015
الوارد

اللون
أحمر
المواصفات

نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك

الحالة
مستعملة
الممشى
147000 كم
المنطقة
الرياض
38,000ريال
1   https://syarah.com/%D9%87%D9%88%D9%86%D8%AF%D8%A7_%D8%B3%D9%8A%D9%81%D9%8A%D9%83_2008/car-10448938
الماركة
هوندا
النوع
سيفيك
الموديل
2008
الوارد

اللون
سلفر
المواصفات

نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك

الحالة
مستعملة
الممشى
450000 كم
المنطقة
الدمام
15,000ريال
2   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%87%D8%A7%D9%8A%D9%84%D9%83%D8%B3_2015/car-10448914
الماركة
تويوتا
النوع
هايلكس
الموديل
2015
الوارد
سعودي
الغمارات
غمارتين
اللون
أبيض
المواصفات

نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك

الحالة
مستعملة
الممشى
205629 كم
المنطقة
الرياض
على السوم
3   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%87%D8%A7%D9%8A%D9%84%D9%83%D8%B3_2016/car-10448590
الماركة
تويوت

20   https://syarah.com/%D8%B4%D9%81%D8%B1%D9%88%D9%84%D9%8A%D9%87_%D8%B3%D9%88%D8%A8%D8%B1%D8%A8%D8%A7%D9%86_2011_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10449608
الماركة
شفروليه
النوع
سوبربان
الفئه
LT
الموديل
2011
الوارد
سعودي
اللون
أسود
المواصفات
نص فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك
8.0
الحالة
مستعملة
الممشى
399 كم
نوع الدفع
دبل (4x4)
المنطقة
الجوف
37,000ريال
21   https://syarah.com/%D9%84%D9%84%D8%A8%D9%8A%D8%B9_%D9%81%D9%88%D8%B1%D8%AF_%D9%81%D9%8A%D8%AC%D9%88_%D9%85%D9%88%D8%AF%D9%8A%D9%84_2017/car-10449606
الماركة
فورد
النوع
فيجو
الفئه
امبيانتي
الموديل
2017
الوارد
سعودي
اللون
أبيض
المواصفات
فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك
1.4
الحالة
مستعملة
الممشى
93000 كم
المنطقة
الرياض
26,000ريال
22   https://syarah.com/%D8%AC%D9%8A_%D8%A5%D9%85_%D8%B3%D9%8A_%D8%B3%D9%88%D8%A8%D8%B1%D8%A8%D8%A7%D9%86_2001_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10449590
الماركة
جي إم سي
النوع
سوبربان
الموديل
2001
الوارد
سعودي
اللون
برونزي
المواصفات
ستاندر
نوع الوقود
بنزين
نوع القير
او

39   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%83%D8%A7%D9%85%D8%B1%D9%8A_%D9%87%D8%A7%D9%8A%D8%A8%D8%B1%D8%AF_2020/car-10449392
الماركة
تويوتا
النوع
كامري
الفئه
GLX
الموديل
2020
الوارد
سعودي
اللون
بني
المواصفات
فل
نوع الوقود
هايبرد/هجين
نوع القير
اوتوماتيك
حجم المحرك

الحالة
مستعملة
الممشى
53000 كم
المنطقة
مكة
على السوم
40   https://syarah.com/%D8%B4%D9%81%D8%B1%D9%88%D9%84%D9%8A%D9%87_%D8%AA%D8%A7%D9%87%D9%88_2012_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10424565
الماركة
شفروليه
النوع
تاهو
الفئه
LT
الموديل
2012
الوارد
سعودي
اللون
ذهبي
المواصفات
نص فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك
5.3
الحالة
مستعملة
الممشى
4691232 كم
نوع الدفع
دبل (4x4)
المنطقة
الجوف
على السوم
41   https://syarah.com/%D8%B4%D9%81%D8%B1%D9%88%D9%84%D9%8A%D9%87_%D8%A8%D9%8A%D9%83_%D8%A7%D8%A8_1981_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10404803
الماركة
شفروليه
النوع
بيك اب
الموديل
1981
الوارد
سعودي
الغمارات
غمارة
اللون
أحمر
المواصفات
فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك
4.5
الحالة

58   https://syarah.com/%D9%85%D8%B1%D8%B3%D9%8A%D8%AF%D8%B3_E_2017_%D9%81%D9%84/car-10341531
الماركة
مرسيدس
النوع
E
الموديل
2017
الوارد
اخرى
اللون
أسود
المواصفات
فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
عدد السلندرات
6
حجم المحرك
3.5
الحالة
مستعملة
الممشى
21000 كم
المنطقة
الدمام
275,000ريال
59   https://syarah.com/%D9%81%D9%88%D8%B1%D8%AF_%D8%A7%D9%83%D8%B3%D8%A8%D8%AF%D8%B4%D9%86_2015_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10449288
الماركة
فورد
النوع
اكسبدشن
الفئه
XLT
الموديل
2015
الوارد
سعودي
اللون
أسود
المواصفات
نص فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك

الحالة
مستعملة
الممشى
225000 كم
نوع الدفع
بدون دبل (4x2)
المنطقة
الرياض
80,000ريال
60   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%83%D8%A7%D9%85%D8%B1%D9%8A_2020_%D9%84%D9%84%D8%AA%D9%86%D8%A7%D8%B2%D9%84/car-10449284
الماركة
تويوتا
النوع
كامري
الفئه
GLI
الموديل
2020
الوارد
سعودي
اللون
أبيض
المواصفات
نص فل
نوع الوقود
هايبرد/هجين
نوع القير
اوتوماتيك
حجم المحرك

الحالة
مستعملة
الممشى
53800 كم
المنطقة
حفر البا

مستعملة
الممشى
51000 كم
المنطقة
الجبيل
2,069ريال شهريا
77   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%84%D8%A7%D9%86%D8%AF%D9%83%D8%B1%D9%88%D8%B2%D8%B1_2013_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10433873
الماركة
تويوتا
النوع
لاندكروزر
الفئه
GX
الموديل
2013
الوارد
سعودي
اللون
أبيض
المواصفات
ستاندر
نوع الوقود
بنزين
نوع القير
عادي
عدد السلندرات
6
حجم المحرك

الحالة
مستعملة
الممشى
422000 كم
نوع الدفع
دبل (4x4)
المنطقة
الدمام
على السوم
78   https://syarah.com/%D9%83%D9%8A%D8%A7_%D8%A7%D9%88%D8%A8%D9%8A%D8%B1%D9%88%D8%B3_2006_Phil_text/car-10390845
الماركة
كيا
النوع
اوبيروس
الموديل
2006
الوارد
اخرى
اللون
لون آخر
المواصفات
نص فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك
3.5
الحالة
مستعملة
الممشى
25500 كم
المنطقة
الرياض
14,000ريال
79   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%8A%D8%A7%D8%B1%D8%B3_2011_%D8%B3%D8%AA%D8%A7%D9%86%D8%AF%D8%B1_%D8%B3%D8%B9%D9%88%D8%AF%D9%8A/car-10438995
الماركة
تويوتا
النوع
يارس
الفئه
أساسي
الموديل
2011
الوارد
سعودي
اللون
لون

...

الماركة
تويوتا
النوع
افالون
الفئه
XLE
الموديل
2016
الوارد
سعودي
اللون
أبيض
المواصفات
نص فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
عدد السلندرات
6
حجم المحرك

الحالة
مستعملة
الممشى
86000 كم
المنطقة
جدة
87,000ريال
3838   https://syarah.com/%D9%87%D9%88%D9%86%D8%AF%D8%A7%D9%8A_%D8%A7%D9%83%D8%B3%D9%86%D8%AA_2010_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10420377
الماركة
هونداي
النوع
اكسنت
الفئه
GL
الموديل
2010
الوارد
اخرى
اللون
أبيض
المواصفات
نص فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك
1.6
الحالة
مستعملة
الممشى
240 كم
المنطقة
الرياض
على السوم
3839   https://syarah.com/%D9%85%D8%B1%D8%B3%D9%8A%D8%AF%D8%B3_S_2012_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10420369
الماركة
مرسيدس
النوع
S
الموديل
2012
الوارد
سعودي
اللون
سلفر
المواصفات
فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
عدد السلندرات
8
حجم المحرك

الحالة
مستعملة
الممشى
140000 كم
المنطقة
الرياض
95,000ريال
3840   https://syarah.com/%D8%B4%D9%81%D8%B1%D9%88%D9%84%D9%8A%D9%87_%D8%B3%D8%A8%D8%A7%D8%B1%D9%83_2019_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-104

3877   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%84%D8%A7%D9%86%D8%AF%D9%83%D8%B1%D9%88%D8%B2%D8%B1_2019_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10419997
3878   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%84%D8%A7%D9%86%D8%AF%D9%83%D8%B1%D9%88%D8%B2%D8%B1_1992_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10419961
3879   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%83%D8%B1%D8%B3%D9%8A%D8%AF%D8%A7_1988_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10419949
3880   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%84%D8%A7%D9%86%D8%AF%D9%83%D8%B1%D9%88%D8%B2%D8%B1_2002_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10419945
3881   https://syarah.com/%D8%AC%D9%8A%D9%86%D9%8A%D8%B3%D9%8A%D8%B3_G80_2017_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10419929
الماركة
جينيسيس
النوع
G80
الفئه
PRESTIGE
الموديل
2017
الوارد
سعودي
اللون
أبيض
المواصفات
فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك
3.8
الحالة
مستعملة
الممشى
158000 كم
المنطقة
القصيم
95,000ريال
3882   https://syarah.com/%

3930   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%81%D9%88%D8%B1%D8%AA%D8%B4%D9%86%D8%B1_GX1_2009_%D8%B3%D8%AA%D8%A7%D9%86%D8%AF%D8%B1/car-10419269
3931   https://syarah.com/%D9%83%D9%8A%D8%A7_%D9%83%D8%A7%D8%AF%D9%8A%D9%86%D8%B2%D8%A7_2020_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10419245
3932   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D8%A7%D9%8A%D9%86%D9%88%D9%81%D8%A7_2015_%D9%81%D9%84_%D9%83%D8%A7%D9%85%D9%84/car-10419229
3933   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%83%D8%B1%D8%B3%D9%8A%D8%AF%D8%A7_1995_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10419199
3934   https://syarah.com/%D9%86%D9%8A%D8%B3%D8%A7%D9%86_%D8%B5%D9%86%D9%8A_2015_%D9%85%D8%AD%D8%B1%D9%83%D8%A9_%D8%B9%D9%84%D9%89_%D8%A7%D8%B4%D8%B1%D8%B7_%D8%B9%D8%B6%D9%84%D8%A7%D8%AA_%D8%B9%D9%84%D9%89_%D8%A7%D8%B4%D8%B1%D8%B7/car-10419187
3935   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%87%D8%A7%D9%8A%D9%84%D9%83%D8%B3_2006_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10419179


3975   https://syarah.com/%D9%87%D9%88%D9%86%D8%AF%D8%A7%D9%8A_%D8%A7%D9%83%D8%B3%D9%86%D8%AA_2017_%D8%B3%D8%AA%D8%A7%D9%86%D8%AF%D8%B1_%D8%B3%D8%B9%D9%88%D8%AF%D9%8A/car-10310634
الماركة
هونداي
النوع
اكسنت
الموديل
2017
الوارد
سعودي
اللون
أبيض
المواصفات
ستاندر
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك

الحالة
مستعملة
الممشى
53000 كم
المنطقة
الدمام
35,000ريال
3976   https://syarah.com/%D9%87%D9%88%D9%86%D8%AF%D8%A7%D9%8A_%D8%A7%D9%83%D8%B3%D9%86%D8%AA_2017_%D8%B3%D8%AA%D8%A7%D9%86%D8%AF%D8%B1_%D8%B3%D8%B9%D9%88%D8%AF%D9%8A/car-10323793
الماركة
هونداي
النوع
اكسنت
الموديل
2017
الوارد
سعودي
اللون
أبيض
المواصفات
ستاندر
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك
1.6
الحالة
مستعملة
الممشى
112000 كم
المنطقة
الدمام
32,000ريال
3977   https://syarah.com/%D9%87%D9%88%D9%86%D8%AF%D8%A7%D9%8A_%D8%A7%D9%83%D8%B3%D9%86%D8%AA_2017_%D8%B3%D8%AA%D8%A7%D9%86%D8%AF%D8%B1_%D8%B3%D8%B9%D9%88%D8%AF%D9%8A/car-10327434
الماركة
هونداي
النوع
اكسنت
الموديل
2017
الوارد
سعودي
اللون
أبيض
المواصفات
ستاندر
ن

32,000ريال
3998   https://syarah.com/%D9%81%D9%88%D8%B1%D8%AF_%D8%A7%D9%83%D8%B3%D8%A8%D9%84%D9%88%D8%B1%D8%B1_2010%D8%B1%D9%82%D9%85_%D8%A7%D9%84%D8%AC%D9%88%D8%A7%D9%84_0500914184/car-10406027
الماركة
فورد
النوع
اكسبلورر
الفئه
سبورت
الموديل
2010
الوارد
اخرى
اللون
أسود
المواصفات
نص فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
حجم المحرك
1.6
الحالة
مستعملة
الممشى
3275230 كم
نوع الدفع
دبل (4x4)
المنطقة
الباحة
على السوم
3999   https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8%AA%D8%A7_%D9%81%D9%88%D8%B1%D8%AA%D8%B4%D9%86%D8%B1_2020_%D9%84%D9%84%D8%A8%D9%8A%D8%B9/car-10399723
الماركة
تويوتا
النوع
فورتشنر
الفئه
GX1
الموديل
2020
الوارد
سعودي
اللون
أبيض
المواصفات
نص فل
نوع الوقود
بنزين
نوع القير
اوتوماتيك
عدد السلندرات
4
حجم المحرك
2.7
الحالة
مستعملة
الممشى
82000 كم
نوع الدفع
بدون دبل (4x2)
المنطقة
مكة
على السوم
4000   https://syarah.com/%D8%AC%D9%8A_%D8%A5%D9%85_%D8%B3%D9%8A_%D9%8A%D9%88%D9%83%D9%86_2019_%D9%84%D9%84%D8%AA%D9%86%D8%A7%D8%B2%D9%84/car-10401496
الماركة
جي إم سي
النوع
يوكن
الفئه
SLT
ا

### Importing dictionary into dataframe

In [372]:
df = pd.DataFrame(data_dict)
df

Link     Make       Type  \
0     https://syarah.com/%D9%83%D8%B1%D8%A7%D9%8A%D8...  كرايسلر       C300   
1     https://syarah.com/%D9%86%D9%8A%D8%B3%D8%A7%D9...    نيسان     باترول   
2     https://syarah.com/online/%D9%86%D9%8A%D8%B3%D...    نيسان        صني   
3     https://syarah.com/online/%D9%87%D9%88%D9%86%D...   هونداي     النترا   
4     https://syarah.com/online/%D9%87%D9%88%D9%86%D...   هونداي     النترا   
...                                                 ...      ...        ...   
8243  https://syarah.com/%D9%84%D9%84%D8%A8%D9%8A%D8...     اودي         A6   
8244  https://syarah.com/%D9%84%D9%84%D8%A8%D9%8A%D8...  شفروليه      كمارو   
8245  https://syarah.com/%D8%AA%D9%88%D9%8A%D9%88%D8...   تويوتا  لاندكروزر   
8246  https://syarah.com/%D9%86%D9%8A%D8%B3%D8%A7%D9...    نيسان     التيما   
8247  https://syarah.com/%D9%83%D8%A7%D8%AF%D9%8A%D9...  كاديلاك       أخرى   

      Year Origin  Color Options Engine Size Fuel Type  Gear Type Condition  \
0     2018  سعودي   أسود      فل         5.7     بنزين  اوتوماتيك   مستعملة   
1     2016  سعودي   أبيض      فل         4.8     بنزين  اوتوماتيك   مستعملة   
2     2019  سعودي   سلفر  ستاندر         1.5     بنزين  اوتوماتيك   مستعملة   
3     2019  سعودي  رمادي  ستاندر         1.6     بنزين  اوتوماتيك   مستعملة   
4     2019  سعودي   سلفر   نص فل         2.0     بنزين  اوتوماتيك   مستعملة   
...    ...    ...    ...     ...         ...       ...        ...       ...   
8243  2015  سعودي   سلفر      فل                 بنزين  اوتوماتيك   مستعملة   
8244  2010  سعودي   سلفر      فل                 بنزين  اوتوماتيك   مستعملة   
8245  2013  خليجي   أبيض      فل                 بنزين  اوتوماتيك   مستعملة   
8246  2011  سعودي   سلفر      فل         2.5     بنزين  اوتوماتيك   مستعملة   
8247  2013  سعودي   أبيض      فل         3.6     بنزين  اوتوماتيك   مستعملة   

     Mileage   Region      Price  
0     103000   الرياض     114000  
1       5448   الرياض  على السوم  
2      72418   الرياض      27500  
3     114154   الرياض      43000  
4      41912   الرياض      59500  
...      ...      ...        ...  
8243   77000   الرياض      75000  
8244  150000   الرياض      53000  
8245     260    نجران  على السوم  
8246   18500     عسير      22000  
8247  256000  المدينة      40000  

[8248 rows x 14 columns]

### Exporting as Excel file

In [373]:
df = pd.DataFrame(data_dict)
df.to_excel("UsedCars_Syarah.xlsx", index=False)

In [ ]:
data_dict = {}
driver.get(link)

data_dict["Link"].append(link)
        
# Get all div elements inside "carDetailesCC"
maindeatils = driver.find_element_by_class_name('carDetailesCC')
divdeatils = maindeatils.find_elements_by_tag_name('div')
        
# Pass all div elements
for l in divdeatils:
lables = l.find_elements_by_tag_name('label') # Get the label
for lable in lables:
print(lable)
values = l.find_elements_by_tag_name('strong') # Get the value
for value in values:
print(value.text)
data_dict[lable].append(value.text)